In [0]:
historical_df = spark.sql("Select * from stocks_ai.stocks_history_data.stock_history_silver_layer")
news_df = spark.sql("Select * from stocks_ai.stocks_news_data.stock_news_silver_layer")
stocks_name_df = spark.sql("Select * from stocks_ai.stocks_name_ticker.stock_names")
holder_df = spark.sql("Select * from stocks_ai.stocks_holders_data.stock_institutional_holders")


In [0]:
%python
from pyspark.sql.functions import collect_list
from pyspark.sql.functions import col, abs, datediff, row_number, to_date
from pyspark.sql.window import Window

grouped_news_df = news_df.groupBy(['date', 'stock']).agg(collect_list('summary').alias('news_list'))
grouped_news_df = grouped_news_df.withColumnRenamed("stock", "ticker")



In [0]:
from pyspark.sql.functions import to_date, col

news_df = grouped_news_df.withColumn("date", to_date(col("date"), "MM-dd-yyyy"))
hist_df = historical_df.withColumn("date", to_date(col("date"), "MM-dd-yyyy"))


news_cols = [c for c in news_df.columns if c not in ['date', 'ticker']]
news_df = news_df.select("date", "ticker", *news_cols)


joined_df = hist_df.alias("hist").join(
    news_df.alias("news"),
    on=["date", "ticker"],
    how="left"  
)


In [0]:
# Perform a left join to add company_name to joined_df
stocks_data_news_historical_df = joined_df.join(
    stocks_name_df, 
    on="ticker", 
    how="left"
)
# Create schema if it doesn't exist
spark.sql("CREATE SCHEMA IF NOT EXISTS stocks_ai.stocks_gold_layer")
stocks_data_news_historical_df.write \
    .format("delta") \
    .mode("overwrite") \
    .saveAsTable("stocks_ai.stocks_GOLD_LAYER.Stocks_news_historical_RAG")


In [0]:
display(stocks_data_news_historical_df)

ticker date close high low open volume news_list company_name MS 2025-06-05 130.62 131.05 127.34 128.37 6193300 List(Wall Street isn't just celebrating the debut of a major stablecoin issuer as Circle's stock soared Thursday. It's also considering how it can compete against Circle in the future., A new investment fund is set to fuel health care services, affordable electricity, and good jobs in rural and tribal areas, offering financing that helps address the multiplying impacts of poverty on the well-being of families and communities., GS doubles down on investment banking, shedding consumer units as M&A leadership and advisory backlog hint at a rebound., (Updates with JPMorgan Chase and TeraWulf's replies in the fifth and sixth paragraphs.) JPMorgan, JPMorgan Chase (JPM) and Morgan Stanley (MS) are arranging a $350 million project financing for Tera, (Bloomberg) -- Delta Air Lines Inc. is planning to sell investment-grade bonds Thursday to help repay a government loan it took out during the pandemic to pay employees.Most Read from BloombergICE Moves to DNA-Test Families Targeted for Deportation with New ContractNext Stop: Rancho Cucamonga!The Global Struggle to Build Safer CarsUS Housing Agency Vulnerable to Fraud After DOGE Cuts, Documents WarnNYC Residents Want Safer Streets, Cheaper Housing, Survey SaysThe airline is marketing three-year, Wells Fargo shares rose over 2% early Wednesday, hitting a three-month high, after the Federal Reserve lifted its asset cap on the bank., (Bloomberg) -- Shares in two of Switzerland’s biggest chocolatiers are on markedly different courses this year as soaring cocoa prices prove a tougher obstacle for one than they do for the other.Most Read from BloombergICE Moves to DNA-Test Families Targeted for Deportation with New ContractThe Global Struggle to Build Safer CarsNYC Residents Want Safer Streets, Cheaper Housing, Survey SaysThe Buffalo Architect Fighting for Women in DesignLindt & Spruengli AG has risen 28% to date as the Lindor, The major Wall Street firms plan to lay off hundreds of workers in June., (Bloomberg) -- Wise Plc is planning to list its shares in the US, the latest loss for London’s stock market after companies worth roughly $100 billion have shifted their primary listings stateside in recent years. Most Read from BloombergICE Moves to DNA-Test Families Targeted for Deportation with New ContractThe Global Struggle to Build Safer CarsNYC Residents Want Safer Streets, Cheaper Housing, Survey SaysThe Buffalo Architect Fighting for Women in DesignWhile the London-based money transfer, Goldman Poaches Rivals’ Marketers in Bid to Grow Fund Management Arm, U.S. companies across sectors haveinitiated layoffs as they attempt to streamline operations amideconomic uncertainties, following similar cutbacks seen lastyear. Job openings — a measure of..., Faced with political uncertainty and mistrust of US assets, the markets are reacting contrary to the usual logic. This is illustrated by the traditional relationship between Treasuries and the dollar....) Morgan Stanley ORCL 2025-06-05 171.14 172.26 168.76 169.0 7707800 List(Zacks.com users have recently been watching Oracle (ORCL) quite a bit. Thus, it is worth knowing the facts that could determine the stock's prospects., (Bloomberg) -- Microsoft Corp. Chief Executive Officer Satya Nadella said his company’s crucial partnership with OpenAI is changing, but remains strong.Most Read from BloombergICE Moves to DNA-Test Families Targeted for Deportation with New ContractThe Global Struggle to Build Safer CarsNYC Residents Want Safer Streets, Cheaper Housing, Survey SaysThe Buffalo Architect Fighting for Women in DesignUS Housing Agency Vulnerable to Fraud After DOGE Cuts, Documents Warn“Any company that has gone from, (Bloomberg) -- US Commerce Secretary Howard Lutnick said the Trump administration has been reworking agreements forged with semiconductor makers under the 2022 Chips Act to secure what he called better terms aimed at generati

In [0]:
# Perform a left join to add company_name to joined_df
holders_final_df= holder_df.join(
    stocks_name_df, 
    on="ticker", 
    how="left"
)
holders_final_df.write \
    .format("delta") \
    .mode("overwrite") \
    .saveAsTable("stocks_ai.stocks_GOLD_LAYER.Stocks_holders_RAG")



In [0]:
display(holders_final_df)

ticker Date_Reported Holder pctHeld Shares Value pctChange company_name AAPL 2025-03-31T00:00:00.000Z Vanguard Group Inc 0.0938 1400790809 280942601233 0.0036000002 Apple Inc. AAPL 2025-03-31T00:00:00.000Z Blackrock Inc. 0.0763 1140202870 228679084823 0.0149 Apple Inc. AAPL 2025-03-31T00:00:00.000Z State Street Corporation 0.0399 596025766 119538926173 9.0000004E-4 Apple Inc. AAPL 2025-03-31T00:00:00.000Z Geode Capital Management, LLC 0.0234 349807156 70157322353 0.028299998 Apple Inc. AAPL 2025-03-31T00:00:00.000Z FMR, LLC 0.022 328100180 65803771299 -0.0396 Apple Inc. AAPL 2025-03-31T00:00:00.000Z Berkshire Hathaway, Inc 0.0201 300000000 60167999267 0.0 Apple Inc. AAPL 2025-03-31T00:00:00.000Z Morgan Stanley 0.0162 241221800 48379443619 0.0124 Apple Inc. AAPL 2025-03-31T00:00:00.000Z Price (T.Rowe) Associates Inc 0.014400001 214703055 43060844186 -0.024600001 Apple Inc. AAPL 2025-03-31T00:00:00.000Z JPMORGAN CHASE & CO 0.013300001 198745598 39860416649 0.086 Apple Inc. AAPL 2024-12-31T00:00:00.000Z NORGES BANK 0.0125 187160162 37536841633 0.0542 Apple Inc. MSFT 2025-03-31T00:00:00.000Z Vanguard Group Inc 0.093 691386214 326655785065 0.0107 Microsoft Corporation MSFT 2025-03-31T00:00:00.000Z Blackrock Inc. 0.0785 583284931 275581712788 0.012200001 Microsoft Corporation MSFT 2025-03-31T00:00:00.000Z State Street Corporation 0.0398 296030244 139863928147 0.0031 Microsoft Corporation MSFT 2025-03-31T00:00:00.000Z FMR, LLC 0.026199998 194591253 91937555636 -0.0148 Microsoft Corporation MSFT 2025-03-31T00:00:00.000Z Geode Capital Management, LLC 0.023599999 175469697 82903289750 0.0437 Microsoft Corporation MSFT 2025-03-31T00:00:00.000Z JPMORGAN CHASE & CO 0.0191 142009968 67094739011 0.052399997 Microsoft Corporation MSFT 2025-03-31T00:00:00.000Z Price (T.Rowe) Associates Inc 0.0177 131514660 62136073355 -0.0269 Microsoft Corporation MSFT 2025-03-31T00:00:00.000Z Morgan Stanley 0.0167 123846555 58513162154 -0.013200001 Microsoft Corporation MSFT 2024-12-31T00:00:00.000Z NORGES BANK 0.014199999 105202984 49704727450 0.0838 Microsoft Corporation MSFT 2025-03-31T00:00:00.000Z Northern Trust Corporation 0.0111 82539834 38997182368 -0.0149 Microsoft Corporation GOOGL 2025-03-31T00:00:00.000Z Vanguard Group Inc 0.0876 509826331 89816103798 0.028900001 Alphabet Inc. GOOGL 2025-03-31T00:00:00.000Z Blackrock Inc. 0.075500004 439591457 77442826174 0.020399999 Alphabet Inc. GOOGL 2025-03-31T00:00:00.000Z State Street Corporation 0.0388 225945895 39804887908 -2.9999999E-4 Alphabet Inc. GOOGL 2025-03-31T00:00:00.000Z FMR, LLC 0.038 221163347 38962346436 -0.1097 Alphabet Inc. GOOGL 2025-03-31T00:00:00.000Z Geode Capital Management, LLC 0.023599999 137390787 24204134694 0.041300002 Alphabet Inc. GOOGL 2024-12-31T00:00:00.000Z NORGES BANK 0.0221 128809703 22692405141 0.1984 Alphabet Inc. GOOGL 2025-03-31T00:00:00.000Z Morgan Stanley 0.0219 127287446 22424229128 0.02 Alphabet Inc. GOOGL 2025-03-31T00:00:00.000Z Price (T.Rowe) Associates Inc 0.0153 89134129 15702759342 -0.0964 Alphabet Inc. GOOGL 2025-03-31T00:00:00.000Z Bank of America Corporation 0.012200001 71240397 12550420609 0.0879 Alphabet Inc. GOOGL 2025-03-31T00:00:00.000Z Northern Trust Corporation 0.0117 68019033 11982912919 -0.023 Alphabet Inc. AMZN 2025-03-31T00:00:00.000Z Vanguard Group Inc 0.0784 832274556 180728414755 0.0108 Amazon.com, Inc. AMZN 2025-03-31T00:00:00.000Z Blackrock Inc. 0.066300005 703411133 152745723237 0.0215 Amazon.com, Inc. AMZN 2025-03-31T00:00:00.000Z State Street Corporation 0.0348 368934077 80114032568 0.0112 Amazon.com, Inc. AMZN 2025-03-31T00:00:00.000Z FMR, LLC 0.032 339634992 73751736439 0.034 Amazon.com, Inc. AMZN 2025-03-31T00:00:00.000Z Geode Capital Management, LLC 0.0201 212995999 46252079882 0.0394 Amazon.com, Inc. AMZN 2025-03-31T00:00:00.000Z JPMORGAN CHASE & CO 0.0189 200228094 43479529390 0.0949 Amazon.com, Inc. AMZN 2025-03-31T00:00:00.000Z Price (T.Rowe) Associates Inc 0.0165 175482278 38105975596 -0.0401 Amazon.com, Inc. AMZN 2025-03-31T00:0